# Define custom functions

This function loads custom Python functions into a table for use by deep learning algorithms.

Custom functions can be useful if, for example, you need loss functions or metrics that are not built into the standard libraries. The functions to be loaded must be in the form of serialized Python objects created using Dill, which extends Python's pickle module to the majority of the built-in Python types.

Custom functions are also used to return top k categorical accuracy rate in the case that you want a different k value than the default from Keras. This module includes a helper function to create the custom function automatically for a specified k.

This method was added in MADlib 1.18.0.

## <em>Warning</em>
<em>For security reasons there are controls on custom functions in MADlib. You must be a superuser to create custom functions because they could theoretically allow execution of any untrusted Python code. Regular users with MADlib USAGE permission can use existing custom functions but cannot create new ones or update existing ones.</em>

## Table of contents

<a href="#load_psycopg2">1. Load object using psycopg2</a>

<a href="#load_plpython">2. Load object using a PL/Python function</a>

<a href="#delete_object">3. Delete object</a>

<a href="#top_k">4. Top k accuracy function</a>

In [1]:
%load_ext sql

In [2]:
# Greenplum Database 5.x on GCP - via tunnel
%sql postgresql://gpadmin@localhost:8000/madlib
        
# PostgreSQL local
#%sql postgresql://fmcquillan@localhost:5432/madlib

In [3]:
%sql select madlib.version();
#%sql select version();

1 rows affected.


[(u'MADlib version: 1.18.0-dev, git revision: rel/v1.17.0-89-g14a91ce, cmake configuration time: Fri Mar  5 23:08:38 UTC 2021, build type: release, build system: Linux-3.10.0-1160.11.1.el7.x86_64, C compiler: gcc 4.8.5, C++ compiler: g++ 4.8.5',)]

<a id="load_psycopg2"></a>
# 1. Load object using psycopg2
Psycopg is a PostgreSQL database adapter for the Python programming language. Note need to use the psycopg2.Binary() method to pass as bytes.

In [4]:
# import database connector psycopg2 and create connection cursor
import psycopg2 as p2
conn = p2.connect('postgresql://gpadmin@localhost:8000/madlib')
cur = conn.cursor()

# import Dill and define functions
import dill

# custom loss
def squared_error(y_true, y_pred):
    import keras.backend as K 
    return K.square(y_pred - y_true)
pb_squared_error=dill.dumps(squared_error)

# custom metric
def rmse(y_true, y_pred):
    import keras.backend as K 
    return K.sqrt(K.mean(K.square(y_pred - y_true), axis=-1))
pb_rmse=dill.dumps(rmse)

# call load function
cur.execute("DROP TABLE IF EXISTS madlib.custom_function_table")
cur.execute("SELECT madlib.load_custom_function('custom_function_table',  %s,'squared_error', 'squared error')", [p2.Binary(pb_squared_error)])
cur.execute("SELECT madlib.load_custom_function('custom_function_table',  %s,'rmse', 'root mean square error')", [p2.Binary(pb_rmse)])
conn.commit()

In [5]:
%%sql
SELECT id, name, description FROM madlib.custom_function_table ORDER BY id;

2 rows affected.


[(1, u'squared_error', u'squared error'),
 (2, u'rmse', u'root mean square error')]

<a id="load_plpython"></a>
# 2. Load object using a PL/Python function

In [6]:
%%sql
CREATE OR REPLACE FUNCTION custom_function_squared_error()
RETURNS BYTEA AS
$$
import dill
def squared_error(y_true, y_pred):
    import tensorflow.keras.backend as K
    return K.square(y_pred - y_true)
pb_squared_error=dill.dumps(squared_error)
return pb_squared_error
$$ language plpythonu;
CREATE OR REPLACE FUNCTION custom_function_rmse()
RETURNS BYTEA AS
$$
import dill
def rmse(y_true, y_pred):
    import tensorflow.keras.backend as K
    return K.sqrt(K.mean(K.square(y_pred - y_true), axis=-1))
pb_rmse=dill.dumps(rmse)
return pb_rmse
$$ language plpythonu;

Done.
Done.


[]

In [7]:
%%sql
DROP TABLE IF EXISTS madlib.custom_function_table;
SELECT madlib.load_custom_function('custom_function_table', 
                                   custom_function_squared_error(), 
                                   'squared_error', 
                                   'squared error');

SELECT madlib.load_custom_function('custom_function_table', 
                                   custom_function_rmse(), 
                                   'rmse', 
                                   'root mean square error');

Done.
1 rows affected.
1 rows affected.


[('',)]

In [8]:
%%sql
SELECT id, name, description FROM madlib.custom_function_table ORDER BY id;

2 rows affected.


[(1, u'squared_error', u'squared error'),
 (2, u'rmse', u'root mean square error')]

<a id="delete_object"></a>
# 3. Delete object
Delete by id:

In [9]:
%%sql
SELECT madlib.delete_custom_function( 'custom_function_table', 1);
SELECT id, name, description FROM madlib.custom_function_table ORDER BY id;

1 rows affected.
1 rows affected.


[(2, u'rmse', u'root mean square error')]

Delete by name:

In [10]:
%%sql
SELECT madlib.delete_custom_function( 'custom_function_table', 'rmse');

1 rows affected.


[('',)]

Since this was the last object in the table, if you delete it then the table will also be dropped.

<a id="top_k"></a>
# 4. Top k accuracy function
Load top 3 accuracy function followed by a top 10 accuracy function:

In [11]:
%%sql
DROP TABLE IF EXISTS madlib.custom_function_table;

SELECT madlib.load_top_k_accuracy_function('custom_function_table',
                                           3);

SELECT madlib.load_top_k_accuracy_function('custom_function_table',
                                           10);

SELECT id, name, description FROM madlib.custom_function_table ORDER BY id;

Done.
1 rows affected.
1 rows affected.
2 rows affected.


[(1, u'top_3_accuracy', u'returns top_3_accuracy'),
 (2, u'top_10_accuracy', u'returns top_10_accuracy')]